This code will load a PiE server trial file and analyze 'frame' events.

Each frame event is logged when the PiE server receives a GPIO frame from a microscope and contains:

    value: frame number
    str: microseconds since start of video recording (frameTimeStamp)
    
Each frameTimeStamp is entirely dependent on the video recording. The idea/rational is that microscope frames trigger a GPIO pin (in bPins) that logs the frame (and its number), then frameTimeStamp can be used to find precisely where that scope frame occured in the video recording.

### Using frameTimeStamp:

Sometimes the frame timestamp is repeated from one frame (GPIO) to the next. I expect this is a true reflection of what is going on in the video file. If the trial file is read and frameTimeStamp is used to advance into the video file (for a given frame in the frameTimeStamp) then this should work. The only problem is when you advance to a frame number, it will sometimes be time-stamped with the previous frame.

### Ignore almost all of this and ...

This is always assuming the GPIO are not entirely missing scope frame pulses. If the GPIO miss a random frame then all frames after that (in the trial file) will be out of sync. In these cases, the first scope frame logged (assuming it is actually the first) can be used as a 'zero' video time and the video can be advanced to scope frame i by moving forward in the video by i*rate where rate is the aquisition rate of the scope.

### Important

Missed GPIO frames occur when the Pi is busy doing somehting else. During recording, limit your interaction with the Pi and in particular the web interface to the PiE server.

### Conclusion

This is very optimistic for the Raspberry Pi, its receiving of GPIO events, and recording video. Again, this is assuming the GPIO are not missing scope frame pulses.


In [14]:
import os
import pandas as pd
import numpy as np

from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import plotly.plotly as py
import plotly.graph_objs as go

init_notebook_mode(connected=True)

import urllib2 # python 2
from StringIO import StringIO # python 2

# Read the trial file from a url on the local PiE server
"""
url = 'http://192.168.1.15:5010/videolist/home/pi/video/20180830/20180830_192310_t1.txt'
response = urllib2.urlopen(url).read()
html = StringIO(response)
"""

# Read the trial file from a local server mount.
# This assumes the Pi is running a file server (afp or smb)
html = '/Volumes/pi15/video/20180902/20180902_185920_t3.txt'
df = pd.read_csv(html, header=1)

# grab the frame events (rows)
frame_df = df[ df['event'].isin(['frame']) ]

# running teensy for 5 minutes yielded 9992 frame
print "Teensy ran for 5 minutes, generating frames at 30 ms interval, yielding 9992 frame'
print "Number of 'frame' events PiE server running on Raspberry detected = ", frame_df.shape[0]

# PiE GPIO missed 9992-9988 = 4 frames in 5 minutes

frame_df[0:9]

Number of 'frame' events PiE server running on Raspberry detected =  9992


date      time  linuxSeconds  secondsSinceStart  event value      str  \
4   20180902  18:59:20  1.535929e+09           0.157021  frame     1  4497581   
5   20180902  18:59:20  1.535929e+09           0.186879  frame     2  4530898   
6   20180902  18:59:20  1.535929e+09           0.217552  frame     3  4564213   
7   20180902  18:59:20  1.535929e+09           0.247236  frame     4  4597529   
8   20180902  18:59:20  1.535929e+09           0.276841  frame     5  4630845   
9   20180902  18:59:20  1.535929e+09           0.307609  frame     6  4664159   
10  20180902  18:59:20  1.535929e+09           0.337181  frame     7  4697475   
11  20180902  18:59:20  1.535929e+09           0.367439  frame     8  4730790   
12  20180902  18:59:20  1.535929e+09           0.397000  frame     9  4730790   

           tick  
4   3355260.294  
5   3355290.295  
6   3355320.295  
7     3355350.3  
8     3355380.3  
9   3355410.305  
10  3355440.305  
11   3355470.31  
12   3355500.31

In [15]:
# microseconds into video recording (when event was logged)
timestampInterval = np.diff( frame_df['str'].astype(float).values ) / 1000 / 1000
# python time the event was logged
timeInterval = np.diff( frame_df['secondsSinceStart'].astype(float).values )
#

frameNumber = frame_df['value'].astype(int).values

#tmp= frame_df[ frame_df['str'].isin(['0']) ]
#print tmp.shape[0]

timestampData = {
        'x': frameNumber, 
        'y': timestampInterval, 
        'text': '', 
        'mode': 'markers', 
        'name': 'timestamp interval'
    }

timeData = {
        'x': frameNumber, 
        'y': timeInterval, 
        'text': '', 
        'mode': 'markers', 
        'name': 'python time interval'
    }

fig = {
    'data': [timeData, timestampData],
    'layout': {
        'xaxis': {'title': 'Frame Number'},
        'yaxis': {'title': "Inter-Frame-Interval (seconds)"}
    }
}

iplot(fig, filename='pandas/multiple-scatter')

In the above plot, timestamp interval is often '0'. This occurs when the frameTimeStamp does not increment from one frame to the next and is presumably a reflection of how the video is actually being recorded. Note, a '0' interval will be followed by a interval that is twice the video recording interval. At 30 fps, a 'good' frame interval is ~33 ms, a double frame interval is ~66 ms.

Remember, frames are being generated by an arduino (e.g. a scope) at 30 ms intervals while video is being recored at 30 fps giving a 'timestamp interval' of 0.0333 seconds.


In [17]:
# frame interval histogram

timestampHist = go.Histogram(x=timestampInterval, name = "video timestamp")
pythonTimeHist = go.Histogram(x=timeInterval, name = "python time")

fig = {
    'data': [pythonTimeHist, timestampHist],
    'layout': {
        'xaxis': {'title': 'Inter-Frame-Interval (seconds)'},
        'yaxis': {'title': "Count", 'type': "log"}
    }
}

iplot(fig, filename='pandas/multiple-scatter')

In [4]:
print 'number of frame intervals = ', timestampInterval.shape[0]

# this assumes we have an even number
interval0 = timestampInterval[0::2]
interval1 = timestampInterval[1::2]

fig = {
    'data': [{
        'x': interval1, 
        'y': interval0, 
        'text': '', 
        'mode': 'markers', 
        'name': 'gpio'
    }],
    'layout': {
        'xaxis': {'title': "Inter-Frame-Interval (seconds)"},
        'yaxis': {'title': 'Previous Inter-Frame-Interval'}
    }
}

iplot(fig, filename='pandas/multiple-scatter')

number of frame intervals =  9987


In [5]:
print 'number of frame intervals = ', timeInterval.shape[0]

# this assumes we have an even number
interval0 = timeInterval[0::2]
interval1 = timeInterval[1::2]

fig = {
    'data': [{
        'x': interval1, 
        'y': interval0, 
        'text': '', 
        'mode': 'markers', 
        'name': 'gpio'
    }],
    'layout': {
        'xaxis': {'title': "Inter-Frame-Interval (seconds)"},
        'yaxis': {'title': 'Previous Inter-Frame-Interval'}
    }
}

iplot(fig, filename='pandas/multiple-scatter')

number of frame intervals =  9987
